## 1. PP-HelixFold模型简介

AlphaFold2是一款高精度的蛋白质结构预测模型。PP-HelixFold基于PaddlePaddle框架在GPU和DCU上完整复现了AlphaFold2的训练和推理流程，并进一步提升模型性能与精度。通过与原版AlphaFold2模型和哥伦比亚大学Mohammed AlQuraishi教授团队基于PyTorch复现的OpenFold模型的性能对比测试显示，PP-HelixFold将训练耗时从约11天减少到7.5天。在性能大幅度提升的同时，PP-HelixFold从头端到端完整训练可以达到AlphaFold2论文媲美的精度。

<p align="center">
<img src="https://github.com/PaddlePaddle/PaddleHelix/blob/dev/.github/HelixFold_computational_performance.png?raw=true" align="middle" height="50%" width="50%" />
<img src="https://github.com/PaddlePaddle/PaddleHelix/blob/dev/.github/HelixFold_accuracy.png?raw=true" align="middle" height="60%" width="60%" />
</p>


## 2. 技术创新

* **分支并行与混合并行策略** PP-HelixFold创新性地提出**分支并行 (Branch Parallelism, BP)** 策略，将不同的网络模型分支放在不同的卡上并行计算，从而在initial training阶段大幅提高了模型并行效率和训练速度。并且，分支并行和已有的**动态轴并行 (Dynamic Axial Parallelism, DAP)** 和**数据并行 (Data Parallelism, DP)** 结合使用，通过BP-DAP-DP三维混合并行，进一步加快了模型的整体训练速度。

* **算子融合优化技术和张量融合低频次访存技术** 针对AlphaFold2中Gated Self-Attention小算子组合CPU调度开销大、模型参数小、参数个数多的问题，PP-HelixFold将Gated Self-Attention整个模块融合用一个算子实现，将CPU调度开销优化到极致。同时，将数千个小张量融合成一个连续的大张量，模型参数的梯度、优化器状态都相应更新，大幅减少了访存次数、CPU调度开销和显存碎片，从而提升了训练速度。

* **多维度显存优化方案** 采用Recompute、BFloat16、显存复用、Subbatch（Chunking）等技术，将显存峰值降低到40G以内，同时支持MSA长度为512、ExtraMSA长度为5120、残基序列长度为384的最大模型配置的微调训练，从而解决了模型结构深，中间结果计算量大，ExtraMSAStack输入过长等导致无法训练的问题。


## 3. 线上服务

如果您想免安装直接尝试使用我们的模型，我们还提供了线上服务器[PaddleHelix HelixFold Forecast](https://paddlehelix.baidu.com/app/drug/protein/forecast)。


## 4. 环境需求

为了能复现我们论文中报告的实验结果，需在特定环境下进行实验。

- python: 3.7
- cuda: 11.2
- cudnn: 8.10.1
- nccl: 2.12.12


## 5. 模型如何使用

### 安装

PP-HelixFold基于[PaddlePaddle](https://github.com/paddlepaddle/paddle)实现。
通过`pip`安装的Python相关库在`requirements.txt`文件中提供，PP-HelixFold需要使用的`openmm==7.5.1`和`pdbfixer`工具，仅可通过`conda`安装。 同时，还需要安装`kalign`、[HH-suite](https://github.com/soedinglab/hh-suite)和`jackhmmer`等工具来生成多序列比对文件。下载脚本需要支持`aria2c`。

我们提供脚本`setup_env`来安装`conda`环境和所需的所有第三方工具库。您可以在`setup_env`中更改环境名字和CUDA版本。运行命令如下：
```bash
git clone https://github.com/PaddlePaddle/PaddleHelix.git # download PaddleHelix
cd /apps/protein_folding/helixfold
wget https://paddle-wheel.bj.bcebos.com/develop/linux/linux-gpu-cuda11.2-cudnn8-mkl-gcc8.2-avx/paddlepaddle_gpu-0.0.0.post112-cp37-cp37m-linux_x86_64.whl
sh setup_env
conda activate helixfold # activate the conda environment
```
注意：如果您环境中的Python3和CUDA版本与我们提供的Paddle whl包不匹配，请参考[这里](https://www.paddlepaddle.org.cn/whl/linux/gpu/develop.html)下载安装对应版本的PaddlePaddle `dev`包。

为了代码运行时支持开启DAP/BP/DP-DAP-BP模式，您还需安装`ppfleetx`。更多详细信息请参考[这里](https://github.com/PaddlePaddle/PaddleFleetX/tree/release/2.4/projects/protein_folding)。
```bash
git clone https://github.com/PaddlePaddle/PaddleFleetX.git
git checkout release/2.4          # change branch
python setup.py develop           # install ppfleetx
```

### 使用

在运行PP-HelixFold前，需要先下载所需的数据库和预训练模型参数。

与原版AlphaFold2一样，您可以运行脚本`scripts/download_all_data.sh`下载所有所需的数据库和预训练模型参数文件：

*   默认选项:

    ```bash
    scripts/download_all_data.sh <DOWNLOAD_DIR>
    ```

    将下载完整版数据库。完整版数据库和预训练模型参数文件的解压前总大小约415 GB，解压后约2.2 TB。

*   `reduced_dbs`选项:

    ```bash
    scripts/download_all_data.sh <DOWNLOAD_DIR> reduced_dbs
    ```

    将下载精简版数据库。精简版数据库和预训练模型参数文件的解压前总大小约190 GB，解压后约530 GB。

### PP-HelixFold模型推理

可以使用如下脚本运行PP-HelixFold模型推理单个或多个蛋白序列文件：

*   在单卡GPU上推理（DP模式）：
    ```bash
    fasta_file="target.fasta"       # path to the target protein
    model_name="model_5"            # the alphafold model name
    DATA_DIR="data"                 # path to the databases
    OUTPUT_DIR="helixfold_output"   # path to save the outputs

    python run_helixfold.py \
      --fasta_paths=${fasta_file} \
      --data_dir=${DATA_DIR} \
      --bfd_database_path=${DATA_DIR}/bfd/bfd_metaclust_clu_complete_id30_c90_final_seq.sorted_opt \
      --small_bfd_database_path=${DATA_DIR}/small_bfd/bfd-first_non_consensus_sequences.fasta \
      --uniclust30_database_path=${DATA_DIR}/uniclust30/uniclust30_2018_08/uniclust30_2018_08 \
      --uniref90_database_path=${DATA_DIR}/uniref90/uniref90.fasta \
      --mgnify_database_path=${DATA_DIR}/mgnify/mgy_clusters_2018_12.fa \
      --pdb70_database_path=${DATA_DIR}/pdb70/pdb70 \
      --template_mmcif_dir=${DATA_DIR}/pdb_mmcif/mmcif_files \
      --obsolete_pdbs_path=${DATA_DIR}/pdb_mmcif/obsolete.dat \
      --max_template_date=2020-05-14 \
      --model_names=${model_name} \
      --output_dir=${OUTPUT_DIR} \
      --preset='reduced_dbs' \
      --jackhmmer_binary_path /opt/conda/envs/helixfold/bin/jackhmmer \
      --hhblits_binary_path /opt/conda/envs/helixfold/bin/hhblits \
      --hhsearch_binary_path /opt/conda/envs/helixfold/bin/hhsearch \
      --kalign_binary_path /opt/conda/envs/helixfold/bin/kalign \
      --random_seed=0
    ```

*   在多卡GPU上推理（DAP模式）：
    ```bash
    fasta_file="target.fasta"       # path to the target protein
    model_name="model_5"            # the alphafold model name
    DATA_DIR="data"                 # path to the databases
    OUTPUT_DIR="helixfold_output"   # path to save the outputs
    log_dir="demo_log"              # path to log file

    distributed_args="--run_mode=collective --log_dir=${log_dir}"
    python -m paddle.distributed.launch ${distributed_args} \
      --gpus="0,1,2,3,4,5,6,7" \
      run_helixfold.py \
      --distributed \
      --dap_degree 8 \
      --fasta_paths=${fasta_file} \
      --data_dir=${DATA_DIR} \
      --bfd_database_path=${DATA_DIR}/bfd/bfd_metaclust_clu_complete_id30_c90_final_seq.sorted_opt \
      --small_bfd_database_path=${DATA_DIR}/small_bfd/bfd-first_non_consensus_sequences.fasta \
      --uniclust30_database_path=${DATA_DIR}/uniclust30/uniclust30_2018_08/uniclust30_2018_08 \
      --uniref90_database_path=${DATA_DIR}/uniref90/uniref90.fasta \
      --mgnify_database_path=${DATA_DIR}/mgnify/mgy_clusters_2018_12.fa \
      --pdb70_database_path=${DATA_DIR}/pdb70/pdb70 \
      --template_mmcif_dir=${DATA_DIR}/pdb_mmcif/mmcif_files \
      --obsolete_pdbs_path=${DATA_DIR}/pdb_mmcif/obsolete.dat \
      --max_template_date=2020-05-14 \
      --model_names=${model_name} \
      --output_dir=${OUTPUT_DIR} \
      --preset='reduced_dbs' \
      --seed 2022 \
      --jackhmmer_binary_path /opt/conda/envs/helixfold/bin/jackhmmer \
      --hhblits_binary_path /opt/conda/envs/helixfold/bin/hhblits \
      --hhsearch_binary_path /opt/conda/envs/helixfold/bin/hhsearch \
      --kalign_binary_path /opt/conda/envs/helixfold/bin/kalign \
      --random_seed=0
    ```
您可以使用命令`python run_helixfold.py -h`查找各参数选项具体描述与定义。

### PP-HelixFold模型在CASP14 Demo上推理

为了使用方便，我们提供一键式运行脚本`gpu_infer.sh`来运行目录`demo_data/casp14_demo`底下的部分CASP14蛋白。您可以运行以下命令来使用：

```bash
sh gpu_infer.sh T1026
```

注意：运行demo蛋白T1026和T1037，您无需下载庞大的数据库，仅需下载预训练模型参数即可使用。


## 6. 相关论文以及引用信息

如果您使用了该代码库里的任何代码和数据，请引用：

```bibtex
@article{AlphaFold2021,
  author={Jumper, John and Evans, Richard and Pritzel, Alexander and Green, Tim and Figurnov, Michael and Ronneberger, Olaf and Tunyasuvunakool, Kathryn and Bates, Russ and {\v{Z}}{\'\i}dek, Augustin and Potapenko, Anna and Bridgland, Alex and Meyer, Clemens and Kohl, Simon A A and Ballard, Andrew J and Cowie, Andrew and Romera-Paredes, Bernardino and Nikolov, Stanislav and Jain, Rishub and Adler, Jonas and Back, Trevor and Petersen, Stig and Reiman, David and Clancy, Ellen and Zielinski, Michal and Steinegger, Martin and Pacholska, Michalina and Berghammer, Tamas and Bodenstein, Sebastian and Silver, David and Vinyals, Oriol and Senior, Andrew W and Kavukcuoglu, Koray and Kohli, Pushmeet and Hassabis, Demis},
  journal={Nature},
  title={Highly accurate protein structure prediction with {AlphaFold}},
  year={2021},
  volume={596},
  number={7873},
  pages={583--589},
  doi={10.1038/s41586-021-03819-2}
}

@article{wang2022helixfold,
  title={HelixFold: An Efficient Implementation of AlphaFold2 using PaddlePaddle},
  author={Wang, Guoxia and Fang, Xiaomin and Wu, Zhihua and Liu, Yiqun and Xue, Yang and Xiang, Yingfei and Yu, Dianhai and Wang, Fan and Ma, Yanjun},
  journal={arXiv preprint arXiv:2207.05477},
  year={2022}
}

@article{wang2022efficient_alphafold2,
  title={Efficient AlphaFold2 Training using Parallel Evoformer and Branch Parallelism},
  author={Wang, Guoxia and Wu, Zhihua and Fang, Xiaomin and Xiang, Yingfei and Liu, Yiqun and Yu, Dianhai and Ma, Yanjun},
  journal={arXiv preprint arXiv:2211.00235},
  year={2022}
}
```

## 7. 版权所有

PP-HelixFold代码使用的是Apache 2.0 License许可文件，该许可与原版AlphaFold2相同。但是，我们使用了由DeepMind提供的AlphaFold2预训练模型参数，根据CC BY-NC 4.0 license许可文件规定，仅可用于非商业用途。
